In [0]:
from pyspark.sql.functions import first, rand, count

# Generowanie dat
dates = spark.sql("SELECT explode(sequence(DATE'2024-01-01', DATE'2024-03-24', INTERVAL 1 DAY)) as calendar_date")

# Generowanie identyfikatorów klientów
c_id = spark.sql("SELECT explode(sequence(1,200, 1)) as client_id")

# Generowanie nazw kolumn
types = spark.sql("""SELECT concat("col_", colName) as col_name FROM (SELECT explode(sequence(1,20, 1)) as colName)""")

# Repartycjonowanie danych
dates = dates.repartition(99)
c_id = c_id.repartition(11)
types = types.repartition(1)

# Tworzenie pełnego cross join
df_cartesian = c_id.crossJoin(dates.select("calendar_date")).crossJoin(types.select("col_name")).select("client_id","calendar_date","col_name")

# Zliczanie liczby klientów dla każdej daty (grupowanie po datach)
df_cartesian2 = df_cartesian.groupBy("calendar_date").agg(count("client_id"))

# display(df_cartesian2.limit(1000))

# Dodanie kolumny z losowymi wartościami (wartość numeryczna)
df_cartesian = df_cartesian.withColumn("val", (rand()*10).cast("int"))

# Tworzenie tabeli z pivotowaniem na kolumnie `col_name`
df_grp = df_cartesian.groupBy("client_id", "calendar_date").pivot("col_name").agg(first("val").alias("val"))

# Wyświetlanie wyników
display(df_grp)

client_id calendar_date col_1 col_10 col_11 col_12 col_13 col_14 col_15 col_16 col_17 col_18 col_19 col_2 col_20 col_3 col_4 col_5 col_6 col_7 col_8 col_9 170 2024-03-19 3 8 0 1 2 9 2 9 4 6 4 3 6 9 0 1 1 5 7 2 170 2024-03-07 5 1 6 9 5 4 9 9 4 5 9 3 4 9 5 9 4 4 5 8 170 2024-01-17 6 8 1 8 1 0 7 4 4 1 3 9 2 3 5 8 8 0 3 2 170 2024-01-31 8 1 6 3 0 9 0 6 7 2 2 5 3 2 9 5 2 9 5 4 170 2024-02-26 0 3 5 2 3 5 9 5 7 4 3 0 7 0 2 2 5 1 2 4 170 2024-03-21 0 0 9 6 3 1 4 6 5 7 3 8 9 0 7 5 7 1 8 2 170 2024-01-29 5 9 7 7 7 2 7 6 3 2 0 3 5 8 1 8 8 4 4 3 170 2024-03-24 1 3 1 8 0 8 4 7 1 0 8 3 4 1 5 1 4 8 0 6 170 2024-02-24 8 3 1 9 9 0 5 6 0 5 8 0 1 4 3 4 6 9 9 6 170 2024-02-29 5 9 4 2 2 5 9 5 6 8 8 2 6 9 2 8 3 2 8 7 170 2024-02-10 2 8 7 9 2 8 6 2 6 7 3 8 2 7 6 3 7 2 7 9 170 2024-02-07 2 8 2 1 7 6 5 3 7 6 9 5 1 5 9 7 3 9 8 1 170 2024-02-27 6 8 4 7 2 9 9 9 4 0 5 4 8 4 5 2 3 6 7 0 170 2024-01-26 1 3 3 4 2 0 4 6 8 6 0 7 5 2 5 4 3 3 7 7 170 2024-01-01 1 5 9 9 5 3 8 5 8 1 5 2 6 8 0 6 8 7 7 4 170 2024-03-01 3 5 2 5 5 1 1 6 4 6 0 6 2 2 3 1 2 4 6 9 170 2024-02-04 4 5 0 0 0 2 8 6 8 3 4 9 0 5 9 0 3 8 4 8 170 2024-01-20 2 7 9 9 9 9 7 7 2 4 0 1 6 2 6 7 8 9 9 8 170 2024-01-19 3 5 2 9 6 5 5 1 7 3 1 0 0 1 3 6 9 7 4 7 170 2024-02-18 9 8 4 0 4 1 7 3 9 3 7 6 1 9 3 8 8 2 3 1 170 2024-03-09 1 9 0 5 6 4 4 1 3 4 5 3 6 8 9 9 7 3 4 4 170 2024-01-10 8 2 6 5 0 8 3 9 4 7 8 3 6 1 6 8 3 6 2 2 170 2024-02-02 5 1 8 4 0 8 0 4 1 1 5 1 8 4 7 4 6 4 9 5 170 2024-02-17 5 8 0 2 0 3 8 0 9 7 8 3 4 3 3 3 1 3 1 4 170 2024-02-15 0 8 5 5 1 8 5 0 1 7 9 3 3 4 9 0 4 4 3 6 170 2024-01-13 6 1 3 6 2 1 4 4 7 5 4 8 0 9 4 8 7 4 2 4 170 2024-01-18 6 1 8 1 5 3 2 1 5 3 3 3 2 9 0 1 6 3 6 5 170 2024-03-10 4 0 4 6 1 2 3 0 6 5 0 0 5 6 6 0 4 1 5 1 170 2024-03-22 9 6 1 8 4 5 7 1 4 5 2 2 8 3 5 6 1 1 0 3 170 2024-03-14 2 4 4 1 6 6 3 6 5 0 1 7 5 0 3 5 3 7 7 0 170 2024-01-15 2 5 5 9 5 8 2 8 5 4 5 5 0 0 1 0 7 4 2 1 170 2024-02-13 2 7 4 5 3 0 1 5 2 4 9 8 4 3 0 4 4 8 9 7 170 2024-01-30 8 5 3 3 7 6 1 0 2 9 8 7 7 7 4 7 4 6 7 6 170 2024-03-16 9 3 6 1 0 5 1 8 0 0 9 9 1 5 1 9 4 8 7 1 170 2024-01-16 6 7 1 5 2 8 8 4 6 2 7 0 4 5 3 9 5 2 0 9 170 2024-03-15 9 2 3 8 3 2 1 1 3 9 9 5 2 1 2 7 7 6 1 8 170 2024-03-17 6 2 1 1 7 3 5 4 4 6 8 0 9 7 3 7 2 0 4 3 170 2024-03-23 7 7 3 0 7 3 8 7 8 1 4 0 1 8 4 9 5 3 6 3 170 2024-02-03 2 6 7 2 7 8 2 1 6 9 2 1 1 9 3 2 2 4 3 1 170 2024-02-14 8 9 5 7 7 9 3 5 9 2 9 4 0 2 3 8 1 8 3 1 170 2024-01-09 8 1 5 2 9 8 3 9 0 8 5 0 4 9 9 5 0 9 7 8 170 2024-02-28 5 3 4 9 5 8 0 0 7 1 3 8 4 5 3 4 1 7 9 6 170 2024-01-12 5 1 1 8 0 4 1 7 6 6 4 9 9 7 7 8 2 5 8 4 170 2024-03-04 2 6 7 2 8 9 8 3 3 7 5 0 3 5 8 0 0 5 2 3 170 2024-02-11 7 9 8 1 9 9 5 1 3 5 6 7 7 6 0 7 3 3 3 9 170 2024-03-03 0 8 9 6 4 1 5 7 5 0 3 5 5 2 8 9 6 1 5 0 170 2024-02-09 5 5 8 1 8 8 4 7 8 8 8 1 4 4 7 5 9 9 2 3 170 2024-03-20 3 5 1 0 2 1 7 0 3 4 4 4 0 7 5 8 5 1 2 7 170 2024-01-08 7 9 7 2 0 9 8 3 5 5 8 6 0 2 0 4 4 7 6 9 170 2024-01-11 7 3 9 3 2 9 5 6 0 2 3 5 5 4 3 4 3 2 8 8 170 2024-03-12 8 5 9 5 5 3 7 8 6 0 6 4 7 2 8 8 3 1 6 1 170 2024-01-03 8 6 1 6 8 4 2 9 3 7 4 3 4 3 3 8 3 9 1 4 170 2024-01-28 7 0 6 1 2 0 8 4 6 8 8 0 8 4 1 5 8 9 4 2 170 2024-02-01 6 6 5 4 0 2 3 0 7 7 4 0 3 8 6 2 9 3 5 2 170 2024-02-16 4 1 7 6 3 9 6 3 6 0 5 9 1 2 6 3 3 8 7 3 170 2024-02-22 5 0 7 5 2 6 6 3 0 6 2 4 1 7 3 7 4 5 2 8 170 2024-02-25 6 7 1 7 6 9 6 3 9 5 5 3 3 2 5 2 2 8 5 4 170 2024-01-07 4 3 1 6 0 8 1 6 1 3 7 6 1 4 7 6 6 9 4 4 170 2024-03-02 7 9 5 5 8 9 4 1 9 4 6 1 9 5 0 3 5 2 3 1 170 2024-03-13 8 3 4 8 8 4 5 6 0 5 7 7 6 8 1 3 6 3 6 9 170 2024-02-08 7 4 7 6 7 9 9 5 8 6 9 6 2 1 2 6 6 4 6 9 170 2024-01-27 0 2 6 0 4 5 3 9 0 3 4 1 3 8 1 0 1 3 0 3 170 2024-01-22 1 5 0 9 1 3 1 2 7 2 5 6 2 7 0 3 1 1 2 1 170 2024-01-23 1 6 1 4 8 7 4 1 9 3 1 5 1 1 4 3 9 1 4 6 170 2024-02-20 1 9 3 2 3 6 5 2 0 8 8 5 8 6 5 5 8 2 1 1 170 2024-03-05 7 4 7 7 8 9 4 8 3 3 3 6 9 7 2 9 2 0 1 2 170 2024-02-06 2 4 0 6 5 1 5 7 7 1 5 5 0 4 3 1 7 3 6 3 170 2024-01-24 1 6 2 3 0 6 0 4 7 7 4 3 2 0 4 4 9 2 0 3 170 2024-01-06 7 4 9 9 8 6 7 4 8 3 3 5 0 5 3 2 6 9 0 5 170 2024-02-23 9 5 9 6 3 2 2 2 7 6 5 5 9 1 3 6 5 1

`inner join` - łączy tylko te wiersze, które mają dopasowane wartości w obu tabelach

`left join` łączy wszystkie wiersze z tabeli po lewej stronie (tutaj df_cartesian), a te, które nie mają dopasowania w tabeli po prawej, dostaną wartości NULL

In [0]:
# zmiana nazwy kolumny, która by się powtarzała
df_cartesian2_renamed = df_cartesian2.withColumnRenamed("calendar_date", "calendar_date_right")

# Złączenie inner
inner_join_result = df_cartesian.join(df_cartesian2_renamed, df_cartesian["calendar_date"] == df_cartesian2_renamed["calendar_date_right"], "inner")

# Usuwanie duplikatów
inner_without_duplicates = inner_join_result.drop("calendar_date_right")

# Wyświetlenie wyników złączenia
display(inner_without_duplicates.limit(10))


client_id calendar_date col_name val count(client_id) 170 2024-03-19 col_1 3 4000 170 2024-03-19 col_2 5 4000 170 2024-03-19 col_3 6 4000 170 2024-03-19 col_4 8 4000 170 2024-03-19 col_5 0 4000 170 2024-03-19 col_6 0 4000 170 2024-03-19 col_7 5 4000 170 2024-03-19 col_8 1 4000 170 2024-03-19 col_9 8 4000 170 2024-03-19 col_10 5 4000

In [0]:
# Złączenie left
left_join_result = df_cartesian.join(df_cartesian2, df_cartesian["calendar_date"] == df_cartesian2["calendar_date"], "left")

# drop "calendar_date"
left_without_duplicates = left_join_result.drop(df_cartesian2["calendar_date"])

display(left_without_duplicates.limit(10))

client_id col_name val calendar_date count(client_id) 170 col_1 3 2024-03-19 4000 170 col_2 5 2024-03-19 4000 170 col_3 6 2024-03-19 4000 170 col_4 8 2024-03-19 4000 170 col_5 0 2024-03-19 4000 170 col_6 0 2024-03-19 4000 170 col_7 5 2024-03-19 4000 170 col_8 1 2024-03-19 4000 170 col_9 8 2024-03-19 4000 170 col_10 5 2024-03-19 4000